In [1]:
ROLE_TOKENS = {
    "human": "<|User|>",     
    "gpt": "<|Assistant|>",   
}
MODEL_NAME = "deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B" 
GRAPH_LENGTH = 512
HF_NAME = "KSU-HW-SEC/r1q1.5_graph_lora_new"

In [2]:
# !pip install transformers accelerate datasets
# !pip install galora
# !pip install huggingface_hub
import torch
print("CUDA 可用:", torch.cuda.is_available())
print("GPU 数量:", torch.cuda.device_count())
print("当前 GPU:", torch.cuda.current_device())
print("GPU 名称:", torch.cuda.get_device_name(torch.cuda.current_device()))

CUDA 可用: True
GPU 数量: 1
当前 GPU: 0
GPU 名称: NVIDIA A100 80GB PCIe


In [3]:
max_seq_length = 1100 + GRAPH_LENGTH  # 最大序列长度

In [4]:
import json
import torch
import os
from transformers import AutoTokenizer
train_data = torch.load("train_data.pt",weights_only=False)
print("train_data 重新加载成功，数据量:", len(train_data))
if 'train_data' not in globals():
    train_data_path = "train_data.pt"
    
    if os.path.exists(train_data_path):  #确保文件存在
        train_data = torch.load(train_data_path, weights_only=False)
        print("train_data 重新加载成功，数据量:", len(train_data))
    else:
        print(f"未找到 {train_data_path}，请检查路径！")
        exit()
#检查是否已经定义了 MODEL_NAME，否则赋值默认值
if "MODEL_NAME" not in globals():
    MODEL_NAME = "deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B"  # 默认模型

tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)


from transformers import Trainer, TrainingArguments, AutoModelForCausalLM

# model = AutoModelForCausalLM.from_pretrained(MODEL_NAME)


from torch.utils.data import Dataset

class GraphDataset(Dataset):
    def __init__(self, data):
        self.data = data

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        sample = self.data[idx]
        return {
            "input_ids": sample["input_ids"],
            "attention_mask": sample["attention_mask"],
            "graph_embedding": sample["graph_embedding"],  # 额外输入
            "labels": sample["labels"],
        }

from transformers import AutoModelForCausalLM, AutoConfig
import torch
import torch.nn as nn

class GraphAwareLM(AutoModelForCausalLM):
    def __init__(self, config):
        super().__init__(config)

        # self.model = AutoModelForCausalLM.from_config(config)
        
        # ✅ 线性变换，把 512 维的 `graph_embedding` 映射到 `hidden_size`
        self.graph_proj = nn.Linear(512, config.hidden_size)

    def forward(self, input_ids=None, attention_mask=None, labels=None, graph_embedding=None):
        """
        `graph_embedding` 形状: (batch_size, 512)
        `input_ids` 形状: (batch_size, seq_len)
        """
        # ✅ 获取 token embedding
        inputs_embeds = self.model.get_input_embeddings()(input_ids)  # (batch_size, seq_len, hidden_size)

        # ✅ 变换 graph embedding 到 hidden_size
        graph_embedding_token = self.graph_proj(graph_embedding)  # (batch_size, hidden_size)

        # ✅ 在 `inputs_embeds` 前面拼接 graph_embedding
        graph_embedding_token = graph_embedding_token.unsqueeze(1)  # (batch_size, 1, hidden_size)
        inputs_embeds = torch.cat([graph_embedding_token, inputs_embeds], dim=1)  # (batch_size, seq_len+1, hidden_size)

        # ✅ 调整 attention mask
        if attention_mask is not None:
            graph_mask = torch.ones((attention_mask.shape[0], 1), device=attention_mask.device, dtype=attention_mask.dtype)
            attention_mask = torch.cat([graph_mask, attention_mask], dim=1)  # (batch_size, seq_len+1)

        # ✅ 传入模型
        outputs = self.model(
            inputs_embeds=inputs_embeds,
            attention_mask=attention_mask,
            labels=labels,
        )

        return outputs

from transformers import Trainer

class GraphTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False, **kwargs):
        input_ids = inputs["input_ids"]
        attention_mask = inputs["attention_mask"]
        labels = inputs["labels"]
        graph_embedding = inputs.get("graph_embedding", None)  

        if graph_embedding is not None:
            outputs = model(
                input_ids=input_ids,
                attention_mask=attention_mask,
                labels=labels,
                graph_embedding=graph_embedding,  
            )
        else:
            outputs = model(
                input_ids=input_ids,
                attention_mask=attention_mask,
                labels=labels,
            )

        loss = outputs.loss
        return (loss, outputs) if return_outputs else loss


from transformers import AutoConfig

# 1. 加载模型的配置
config = AutoConfig.from_pretrained(MODEL_NAME)

# 2. 使用配置创建 GraphAwareLM 实例
model = GraphAwareLM.from_config(config) 

pretrained_model = AutoModelForCausalLM.from_pretrained(MODEL_NAME)
model.load_state_dict(pretrained_model.state_dict(), strict=False)

# ✅ 载入修改后的 `GraphAwareLM` 模型
# model = GraphAwareLM.from_pretrained(MODEL_NAME)
# model.config.use_sliding_window_attention = False

# ✅ 训练参数
training_args = TrainingArguments(
    output_dir="./results",
    per_device_train_batch_size=7,
    eval_strategy="no",
    save_strategy="steps",
    save_steps=3000,
    logging_steps=50,
    bf16=True,
    optim="galore_adamw",
    optim_target_modules="all-linear",  # ✅ 让 GaLore 作用于所有线性层
    optim_args="rank=128,scale=2.0",  # ✅ 低秩分解参数
    warmup_steps=1000,
    num_train_epochs=3,
    push_to_hub=True,
    hub_model_id=HF_NAME,
    hub_strategy="every_save",
    run_name = "experi0304"
)


# ✅ 转换 `train_data` 为 `Dataset`
train_dataset = GraphDataset(train_data)

# ✅ 训练
trainer = GraphTrainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
)

trainer.train()
trainer.save_model("/workspace/model")
trainer.push_to_hub()




train_data 重新加载成功，数据量: 12384


Sliding Window Attention is enabled but not implemented for `eager`; unexpected results may be encountered.
/usr/local/lib/python3.10/dist-packages/galore_torch/adamw.py:48: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: 675775971 (yifang_zhao) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


No files have been modified since last commit. Skipping to prevent empty commit.


CommitInfo(commit_url='https://huggingface.co/KSU-HW-SEC/r1q1.5_graph_lora_new/commit/231f89403dca9aa67966e4f321e62bdb41076960', commit_message='End of training', commit_description='', oid='231f89403dca9aa67966e4f321e62bdb41076960', pr_url=None, repo_url=RepoUrl('https://huggingface.co/KSU-HW-SEC/r1q1.5_graph_lora_new', endpoint='https://huggingface.co', repo_type='model', repo_id='KSU-HW-SEC/r1q1.5_graph_lora_new'), pr_revision=None, pr_num=None)

In [5]:
import json
import torch
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
tokenizer.pad_token = tokenizer.eos_token  

json_path = "final_Graph.json"
with open(json_path, "r") as f:
    data = json.load(f)

train_data = []


for sample in data:
    conversations = sample.get("conversations", [])
    embeddings = sample.get("embedding", []) 

    if not isinstance(embeddings, list) or len(embeddings) == 0:
        print(f"无效的 embedding，跳过样本：{sample}")
        continue

    graph_embedding = torch.tensor(embeddings, dtype=torch.float32).squeeze(0)  # [512]

    #拼接所有对话
    dialogue_text = ""
    for conv in conversations:
        role = conv["from"]  # "human" 或 "gpt"
        content = conv["value"]
        content = content.replace("<image>", "") #去掉 <image>
        role_token = ROLE_TOKENS.get(role, f"<|{role}|>")  # 兼容性处理
        dialogue_text += f"{role_token} {content}\n"

    tokenized = tokenizer(
        dialogue_text,
        padding="max_length",
        truncation=True,
        max_length=max_seq_length - GRAPH_LENGTH,  # 预留 graph embedding 空间
        return_tensors="pt",
    )

    input_ids = tokenized["input_ids"].squeeze(0)
    attention_mask = tokenized["attention_mask"].squeeze(0)

    train_data.append({
        "input_ids": input_ids,
        "attention_mask": attention_mask,
        "labels": input_ids.clone(),
        "graph_embedding": graph_embedding,  # `graph_embedding` 存入
    })

print("🚀 处理后数据条数:", len(train_data))
print("✅ 示例数据:", train_data[0])
torch.save(train_data, "train_data.pt")
print("✅ train_data 已保存到 train_data.pt")


🚀 处理后数据条数: 12384
✅ 示例数据: {'input_ids': tensor([151643, 151643, 151643,  ...,   1493,   7525,    624]), 'attention_mask': tensor([0, 0, 0,  ..., 1, 1, 1]), 'labels': tensor([151643, 151643, 151643,  ...,   1493,   7525,    624]), 'graph_embedding': tensor([-2.4214, -0.5552,  1.0389, -1.3428, -0.1341,  0.6100, -0.4200, -1.8584,
        -0.2880, -0.4779,  0.3452, -0.8934, -0.9216,  0.5600,  0.2474, -0.9009,
        -1.0995,  0.6065,  1.7662, -1.2281,  0.0000, -1.9196,  0.1920, -1.2770,
        -0.6918, -1.3762, -0.7639, -0.1023,  2.5149,  1.1990, -0.2678, -0.7488,
        -0.0000,  0.9108,  0.2010, -0.2639,  0.5023, -0.8752,  0.2083,  0.5740,
         0.3758, -0.7036, -1.3210, -0.8119, -0.5329, -0.2355, -0.2750,  1.6133,
        -2.3233,  0.3174,  0.0000,  0.5769,  0.3558,  0.2234, -0.0666, -0.6310,
        -0.3533,  0.9497, -0.9576,  0.1615, -0.0460, -1.1686,  1.4337, -1.2952,
        -1.1095,  0.5081, -1.9626, -0.3278,  0.7837, -2.4616,  0.3936, -0.3157,
        -1.6531, -0.0708, -0.663

In [6]:
import json
import torch
import os
from transformers import AutoTokenizer
train_data = torch.load("train_data.pt",weights_only=False)
print("train_data 重新加载成功，数据量:", len(train_data))
if 'train_data' not in globals():
    train_data_path = "train_data.pt"
    
    if os.path.exists(train_data_path):  #确保文件存在
        train_data = torch.load(train_data_path, weights_only=False)
        print("train_data 重新加载成功，数据量:", len(train_data))
    else:
        print(f"未找到 {train_data_path}，请检查路径！")
        exit()
#检查是否已经定义了 MODEL_NAME，否则赋值默认值
if "MODEL_NAME" not in globals():
    MODEL_NAME = "deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B"  # 默认模型

tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)


from transformers import Trainer, TrainingArguments, AutoModelForCausalLM

model = AutoModelForCausalLM.from_pretrained(MODEL_NAME)


from torch.utils.data import Dataset

class GraphDataset(Dataset):
    def __init__(self, data):
        self.data = data

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        sample = self.data[idx]
        return {
            "input_ids": sample["input_ids"],
            "attention_mask": sample["attention_mask"],
            "graph_embedding": sample["graph_embedding"],  # 额外输入
            "labels": sample["labels"],
        }

from transformers import AutoModelForCausalLM
import torch
import torch.nn as nn

class GraphAwareLM(AutoModelForCausalLM):
    def __init__(self, config):
        super().__init__(config)
        self.model = AutoModelForCausalLM.from_pretrained(config)
        
        # ✅ 线性变换，把 512 维的 `graph_embedding` 映射到 `hidden_size`
        self.graph_proj = nn.Linear(512, config.hidden_size)

    def forward(self, input_ids=None, attention_mask=None, labels=None, graph_embedding=None):
        """
        `graph_embedding` 形状: (batch_size, 512)
        `input_ids` 形状: (batch_size, seq_len)
        """
        # ✅ 获取 token embedding
        inputs_embeds = self.model.get_input_embeddings()(input_ids)  # (batch_size, seq_len, hidden_size)

        # ✅ 变换 graph embedding 到 hidden_size
        graph_embedding_token = self.graph_proj(graph_embedding)  # (batch_size, hidden_size)

        # ✅ 在 `inputs_embeds` 前面拼接 graph_embedding
        graph_embedding_token = graph_embedding_token.unsqueeze(1)  # (batch_size, 1, hidden_size)
        inputs_embeds = torch.cat([graph_embedding_token, inputs_embeds], dim=1)  # (batch_size, seq_len+1, hidden_size)

        # ✅ 调整 attention mask
        if attention_mask is not None:
            graph_mask = torch.ones((attention_mask.shape[0], 1), device=attention_mask.device, dtype=attention_mask.dtype)
            attention_mask = torch.cat([graph_mask, attention_mask], dim=1)  # (batch_size, seq_len+1)

        # ✅ 传入模型
        outputs = self.model(
            inputs_embeds=inputs_embeds,
            attention_mask=attention_mask,
            labels=labels,
        )

        return outputs

from transformers import Trainer

class GraphTrainer(Trainer):
    def compute_loss(self, model, inputs, return_outputs=False, **kwargs):
        input_ids = inputs["input_ids"]
        attention_mask = inputs["attention_mask"]
        labels = inputs["labels"]
        graph_embedding = inputs.get("graph_embedding", None)  

        if graph_embedding is not None:
            outputs = model(
                input_ids=input_ids,
                attention_mask=attention_mask,
                labels=labels,
                graph_embedding=graph_embedding,  
            )
        else:
            outputs = model(
                input_ids=input_ids,
                attention_mask=attention_mask,
                labels=labels,
            )

        loss = outputs.loss
        return (loss, outputs) if return_outputs else loss



# ✅ 载入修改后的 `GraphAwareLM` 模型
model = GraphAwareLM.from_pretrained(MODEL_NAME)
# model.config.use_sliding_window_attention = False

# ✅ 训练参数
training_args = TrainingArguments(
    output_dir="./results",
    per_device_train_batch_size=7,
    eval_strategy="no",
    save_strategy="steps",
    save_steps=3000,
    logging_steps=50,
    fp16=True,
    optim="galore_adamw",
    optim_target_modules="all-linear",  # ✅ 让 GaLore 作用于所有线性层
    optim_args="rank=128,scale=2.0",  # ✅ 低秩分解参数
    warmup_steps=1000,
    num_train_epochs=3,
    push_to_hub=True,
    hub_model_id=HF_NAME,
    hub_strategy="every_save",
    run_name = "experi0304"
)


# ✅ 转换 `train_data` 为 `Dataset`
train_dataset = GraphDataset(train_data)

# ✅ 训练
trainer = GraphTrainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
)

trainer.train()
trainer.push_to_hub()
trainer.save_model("/workspace/model")



train_data 重新加载成功，数据量: 12384


Sliding Window Attention is enabled but not implemented for `eager`; unexpected results may be encountered.
/usr/local/lib/python3.10/dist-packages/galore_torch/adamw.py:49: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: 675775971 (yifang_zhao) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


KeyboardInterrupt: 

In [1]:
from transformers import AutoModelForCausalLM
import torch
import torch.nn as nn

class GraphAwareLM(AutoModelForCausalLM):

    
    def __init__(self, config):
        super().__init__(config)
        self.graph_proj = nn.Linear(512, config.hidden_size)

    def forward(self, input_ids=None, attention_mask=None, labels=None, graph_embedding=None):
        """
        `graph_embedding` 形状: (batch_size, 512)
        `input_ids` 形状: (batch_size, seq_len)
        """
        # ✅ 获取 token embedding
        inputs_embeds = self.get_input_embeddings()(input_ids)  # (batch_size, seq_len, hidden_size)

        # ✅ 变换 graph embedding 到 hidden_size
        graph_embedding_token = self.graph_proj(graph_embedding.squeeze(0))  # (batch_size, hidden_size)

        # ✅ 在 `inputs_embeds` 前面拼接 graph_embedding
        graph_embedding_token = graph_embedding_token.unsqueeze(1)  # (batch_size, 1, hidden_size)
        inputs_embeds = torch.cat([graph_embedding_token, inputs_embeds], dim=1)  # (batch_size, seq_len+1, hidden_size)

        # ✅ 调整 attention mask
        if attention_mask is not None:
            graph_mask = torch.ones((attention_mask.shape[0], 1), device=attention_mask.device, dtype=attention_mask.dtype)
            attention_mask = torch.cat([graph_mask, attention_mask], dim=1)  # (batch_size, seq_len+1)

        # ✅ 传入模型
        outputs = self.model(
            inputs_embeds=inputs_embeds,
            attention_mask=attention_mask,
            labels=labels,
        )

        return outputs

    @classmethod
    def from_pretrained(cls, pretrained_model_name_or_path, *model_args, **kwargs):
        model = super().from_pretrained(pretrained_model_name_or_path, *model_args, **kwargs)
        model.graph_proj = nn.Linear(512, model.config.hidden_size)
        return model


In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [3]:
import torch
from transformers import AutoTokenizer

# 加载 tokenizer
MODEL_NAME = "deepseek-ai/DeepSeek-R1-Distill-Qwen-1.5B"
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)

# 加载训练好的模型
model_path = "/workspace/model"
model = GraphAwareLM.from_pretrained(model_path).to(device)
model.eval()  # 设置为推理模式


Sliding Window Attention is enabled but not implemented for `eager`; unexpected results may be encountered.


Qwen2ForCausalLM(
  (model): Qwen2Model(
    (embed_tokens): Embedding(151936, 1536)
    (layers): ModuleList(
      (0-27): 28 x Qwen2DecoderLayer(
        (self_attn): Qwen2Attention(
          (q_proj): Linear(in_features=1536, out_features=1536, bias=True)
          (k_proj): Linear(in_features=1536, out_features=256, bias=True)
          (v_proj): Linear(in_features=1536, out_features=256, bias=True)
          (o_proj): Linear(in_features=1536, out_features=1536, bias=False)
        )
        (mlp): Qwen2MLP(
          (gate_proj): Linear(in_features=1536, out_features=8960, bias=False)
          (up_proj): Linear(in_features=1536, out_features=8960, bias=False)
          (down_proj): Linear(in_features=8960, out_features=1536, bias=False)
          (act_fn): SiLU()
        )
        (input_layernorm): Qwen2RMSNorm((1536,), eps=1e-06)
        (post_attention_layernorm): Qwen2RMSNorm((1536,), eps=1e-06)
      )
    )
    (norm): Qwen2RMSNorm((1536,), eps=1e-06)
    (rotary_emb): Qw

In [8]:
import json
json_path = "final_Graph.json"
with open(json_path, "r") as f:
    data = json.load(f)

test_data = data[0]

conversations = test_data.get("conversations")
embeddings = test_data.get("embedding") 

graph_embedding = torch.tensor(embeddings, dtype=torch.float32).to(device)

question1 = conversations[4]["value"].replace("<image>", "").strip()

from transformers import AutoTokenizer

# ✅ 输入文本
ROLE_TOKENS = {
    "human": "<|User|>",     
    "gpt": "<|Assistant|>",   
}
GRAPH_LENGTH = 512
max_seq_length = 1100 + GRAPH_LENGTH
inputs = tokenizer(question1, return_tensors="pt",truncation=True,max_length=max_seq_length - GRAPH_LENGTH).to(device)

input_ids = inputs["input_ids"]
attention_mask = inputs["attention_mask"]


In [5]:
graph_embedding

tensor([[-2.4214, -0.5552,  1.0389, -1.3428, -0.1341,  0.6100, -0.4200, -1.8584,
         -0.2880, -0.4779,  0.3452, -0.8934, -0.9216,  0.5600,  0.2474, -0.9009,
         -1.0995,  0.6065,  1.7662, -1.2281,  0.0000, -1.9196,  0.1920, -1.2770,
         -0.6918, -1.3762, -0.7639, -0.1023,  2.5149,  1.1990, -0.2678, -0.7488,
         -0.0000,  0.9108,  0.2010, -0.2639,  0.5023, -0.8752,  0.2083,  0.5740,
          0.3758, -0.7036, -1.3210, -0.8119, -0.5329, -0.2355, -0.2750,  1.6133,
         -2.3233,  0.3174,  0.0000,  0.5769,  0.3558,  0.2234, -0.0666, -0.6310,
         -0.3533,  0.9497, -0.9576,  0.1615, -0.0460, -1.1686,  1.4337, -1.2952,
         -1.1095,  0.5081, -1.9626, -0.3278,  0.7837, -2.4616,  0.3936, -0.3157,
         -1.6531, -0.0708, -0.6630,  0.4285,  0.1360, -0.7986, -0.1449,  0.0000,
          0.9076,  0.7794,  0.6391,  0.9840,  0.2970,  1.5463,  1.1554, -0.5432,
          0.7202,  0.0000, -0.2380,  0.0422,  0.0000,  0.4296,  0.2068,  0.3330,
         -0.5888,  0.0000,  

In [15]:
# ✅ 进行前向传播
with torch.no_grad():
    outputs = model(input_ids=input_ids, attention_mask=attention_mask, graph_embedding=graph_embedding)

# ✅ 提取 logits 并进行贪心解码
logits = outputs.logits[:, -1, :]  # 取最后一个 token 的 logits
predicted_id = torch.argmax(logits, dim=-1)  # 选择概率最大的 token

# ✅ 反向编码为文本
response_text = tokenizer.decode(predicted_id, skip_special_tokens=True)

print("模型回复：", response_text)

模型回复：  How


In [9]:
max_new_tokens = 1024
generated_ids = input_ids.clone()
generated_attention_mask = attention_mask.clone()
for _ in range(max_new_tokens):
    # ✅ 计算 logits 并进行生成
    with torch.no_grad():
        outputs = model(
            input_ids=generated_ids,        # (batch_size, seq_len)
            attention_mask=generated_attention_mask,  # (batch_size, seq_len)
            graph_embedding=graph_embedding,      # (batch_size, 512)
        )


    logits = outputs.logits[:, -1, :]  # 取最后一个 token 的 logits
    next_token = torch.argmax(logits, dim=-1)  # 贪心解码
    # print(next_token)


    # ✅ **拼接到已生成序列**
    generated_ids = torch.cat([generated_ids, next_token.unsqueeze(1)], dim=1)

    # print(generated_ids)

    if next_token.item() == tokenizer.eos_token_id:
        break

    generated_attention_mask = torch.cat(
        [generated_attention_mask, torch.ones((1, 1), dtype=generated_attention_mask.dtype, device=generated_attention_mask.device)], dim=1
    ) 

# ✅ 解码最终输出
generated_text = tokenizer.decode(generated_ids[0], skip_special_tokens=True)
print("Generated Response:", generated_text)

Generated Response: Is there any sequential logic in the module, and if so, how is it handled? What are the module's inputs and outputs?
What are the module's inputs and outputs?
What are the module's inputs and outputs?
What are the module's inputs and outputs?
What is the module's input, and what is the module's output, and what is the module's output, and what is the module's input, and what is the module's output, and what is the module's input, and what is the module's output, and what is the module's input, and what is the module's output, and what is the module's output, and what is the module's input, and what is the module's output, and what is the module's output, and what is the module's input, and what is the module's output, and what is the module's output, and what is the module's output, and what is the module's output, and what is the module's output, and module's output, and module's input, and module's output, and module's output, and module's output, and module's out

In [10]:
generated_ids

tensor([[151646,   3838,    525,    279,   8286,  17473,    304,    279,   6250,
          50773,   2038,    369,    279,  29952,   4688,     11,    323,   1128,
            525,    862,   9895,     30]], device='cuda:0')